<a href="https://colab.research.google.com/github/Requenamar3/Data-Mining/blob/main/Data_Mining_Module1_Ecommerce_CLV.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Customer Lifetime Value model

In [1]:
#package used for customer lifetime value modeling
!pip install lifetimes

In [2]:
 # installing the pandas_profiling package for data analysis and generating statistical report summaries.
!pip install ydata_profiling


In [3]:
# Customer Lifetime Value (CLV or CLTV)
# Buy till you die... (BG/NBD)

# Import the lifetimes package for customer lifetime value analysis.
import lifetimes
# Import pandas for data manipulation and analysis.
import pandas as pd
# Import numpy for numerical computing.
import numpy as np
# Import datetime for handling dates and times.
import datetime as dt
# Import matplotlib.pyplot for creating static, animated, and interactive visualizations.
import matplotlib.pyplot as plt
# Import seaborn for making statistical graphics.
import seaborn as sns
# Import BetaGeoFitter from lifetimes for fitting the BG/NBD model.
from lifetimes import BetaGeoFitter
# Import GammaGammaFitter from lifetimes for fitting the Gamma-Gamma model.
from lifetimes import GammaGammaFitter
# Import plot_frequency_recency_matrix for visualizing the relationship between frequency and recency.
from lifetimes.plotting import plot_frequency_recency_matrix

# Set pandas display options to improve the readability of output.
# Set the maximum number of rows to display to 500.
pd.set_option('display.max_rows', 500)
# Set the maximum number of columns to display to 500.
pd.set_option('display.max_columns', 500)
# Set the width of the display in characters to 1000.
pd.set_option('display.width', 1000)


In [4]:
#Import the ProfileReport .For creating comprehensive exploratory data analysis reports.
from ydata_profiling import ProfileReport

In [14]:
EC= pd.read_csv("https://raw.githubusercontent.com/Requenamar3/Data-Mining/main/sales_2023-11-01_2024-03-05.csv")

In [15]:
EC.head()

month    financial_status order_name             customer_email customer_type    customer_id variant_sku   product_title shipping_postal_code shipping_region customer_cohort_month  total_sales  ordered_item_quantity
0  2023-11                paid    #826267        amansndrs@gmail.com     Returning  6816167329907         NaN             NaN                71254       Louisiana               2023-08         0.00                      0
1  2023-11                paid    #821120          jsajcat@gmail.com     Returning  6882693939315   SQ1726938  Bloomsy Deluxe                60101        Illinois               2023-09        76.98                      1
2  2023-11                paid    #825181        amymattey@gmail.com     Returning  3492230627443         NaN             NaN                44035            Ohio               2020-11        83.88                      0
3  2023-11  partially_refunded    #793583  kathryndonnelly@yahoo.com     Returning  6536856797299         NaN             NaN                60555        Illinois               2023-03      -162.24                      0
4  2023-11  partially_refunded    #814967  nancynetherland@gmail.com     Returning  5686113435763         NaN             NaN                98502      Washington               2022-05       -91.44                      0

In [7]:
# Create a ProfileReport object
profile = ProfileReport(EC, title="EC CLV", explorative=True)

In [8]:
# display report
profile


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [16]:
# Remove the '#' from the 'order_name' column
EC['order_name'] = EC['order_name'].str.replace('#', '')


In [17]:
#remove all but paid from finalcial_status
EC = EC[EC['financial_status'] == 'paid']


In [19]:
# Remove rows from 'EC' where 'total_sales' is equal to 0.00
EC = EC[EC['total_sales'] != 0.00]


In [24]:
# Find duplicate 'order_name' in 'EC'
duplicates = EC[EC.duplicated('order_name', keep=False)]

# Count the total number of duplicate 'order_name' entries
total_duplicate_count = duplicates['order_name'].count()

# Display the count of total duplicates
print(f"Total number of duplicate 'order_name' entries: {total_duplicate_count}")

# Display the duplicate rows
print(duplicates)


Total number of duplicate 'order_name' entries: 52174
          month financial_status order_name            customer_email customer_type    customer_id variant_sku      product_title shipping_postal_code shipping_region customer_cohort_month  total_sales  ordered_item_quantity
2       2023-11             paid     825181       amymattey@gmail.com     Returning  3492230627443         NaN                NaN                44035            Ohio               2020-11        83.88                      0
248     2023-11             paid     817616        kwebb820@gmail.com     Returning  6565802016883         NaN                NaN           20136-2226        Virginia               2023-04        20.97                      0
249     2023-11             paid     817616        kwebb820@gmail.com     Returning  6565802016883   SQ5173256  Bloomsy Bi-Weekly           20136-2226        Virginia               2023-04       158.97                      1
252     2023-11             paid     812987   

In [27]:
# Filter the DataFrame to find all records with 'order_name' equal to '839382'
records_with_order_name_839382 = EC[EC['order_name'] == '839382']

# Display the records
print(records_with_order_name_839382)


         month financial_status order_name                customer_email customer_type    customer_id variant_sku         product_title shipping_postal_code shipping_region customer_cohort_month  total_sales  ordered_item_quantity
28741  2023-12             paid     839382  victoriakcolangelo@gmail.com    First-time  7097201131635     BB1284P        Pink Bromeliad                32708         Florida               2023-12        59.99                      1
41065  2023-12             paid     839382  victoriakcolangelo@gmail.com    First-time  7097201131635     BB1404P       Fiddle Leaf Fig                32708         Florida               2023-12        64.19                      1
41069  2023-12             paid     839382  victoriakcolangelo@gmail.com    First-time  7097201131635     CLIPPER      Florist Clippers                32708         Florida               2023-12        29.94                      2
54216  2023-12             paid     839382  victoriakcolangelo@gmail.com    

In [25]:
# Remove records with 0 orders qty
EC = EC[EC['ordered_item_quantity'] != 0]


In [26]:
EC.head()

month financial_status order_name                 customer_email customer_type    customer_id variant_sku      product_title shipping_postal_code shipping_region customer_cohort_month  total_sales  ordered_item_quantity
1    2023-11             paid     821120              jsajcat@gmail.com     Returning  6882693939315   SQ1726938     Bloomsy Deluxe                60101        Illinois               2023-09        76.98                      1
43   2023-11             paid     826267            amansndrs@gmail.com     Returning  6816167329907   SQ9178530   Bloomsy Original                71254       Louisiana               2023-08        66.86                      1
249  2023-11             paid     817616             kwebb820@gmail.com     Returning  6565802016883   SQ5173256  Bloomsy Bi-Weekly           20136-2226        Virginia               2023-04       158.97                      1
253  2023-11             paid     812987             miberkst@gmail.com     Returning  3039319621747   SQ8862610    Bloomsy Premium                80212        Colorado               2020-05        60.11                      1
257  2023-11             paid     813054  heather.dlugolenski@yahoo.com     Returning  3284875477107   SQ8862610    Bloomsy Premium                06026     Connecticut               2020-08       171.21                      1

In [28]:
EC.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36931 entries, 1 to 131973
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   month                  36931 non-null  object 
 1   financial_status       36931 non-null  object 
 2   order_name             36931 non-null  object 
 3   customer_email         36829 non-null  object 
 4   customer_type          36931 non-null  object 
 5   customer_id            36931 non-null  int64  
 6   variant_sku            36914 non-null  object 
 7   product_title          36931 non-null  object 
 8   shipping_postal_code   36931 non-null  object 
 9   shipping_region        36931 non-null  object 
 10  customer_cohort_month  36931 non-null  object 
 11  total_sales            36931 non-null  float64
 12  ordered_item_quantity  36931 non-null  int64  
dtypes: float64(1), int64(2), object(10)
memory usage: 3.9+ MB


In [33]:
EC.isnull().sum()

month                      0
financial_status           0
order_name                 0
customer_email           102
customer_type              0
customer_id                0
variant_sku               17
product_title              0
shipping_postal_code       0
shipping_region            0
customer_cohort_month      0
total_sales                0
ordered_item_quantity      0
dtype: int64

In [34]:
EC.dropna(inplace=True)  # inplace=True means we dropped them permanently

In [35]:
EC.isnull().sum()

month                    0
financial_status         0
order_name               0
customer_email           0
customer_type            0
customer_id              0
variant_sku              0
product_title            0
shipping_postal_code     0
shipping_region          0
customer_cohort_month    0
total_sales              0
ordered_item_quantity    0
dtype: int64

In [37]:
EC.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36812 entries, 1 to 131973
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   month                  36812 non-null  object 
 1   financial_status       36812 non-null  object 
 2   order_name             36812 non-null  object 
 3   customer_email         36812 non-null  object 
 4   customer_type          36812 non-null  object 
 5   customer_id            36812 non-null  int64  
 6   variant_sku            36812 non-null  object 
 7   product_title          36812 non-null  object 
 8   shipping_postal_code   36812 non-null  object 
 9   shipping_region        36812 non-null  object 
 10  customer_cohort_month  36812 non-null  object 
 11  total_sales            36812 non-null  float64
 12  ordered_item_quantity  36812 non-null  int64  
dtypes: float64(1), int64(2), object(10)
memory usage: 3.9+ MB


In [38]:
EC.describe()

customer_id   total_sales  ordered_item_quantity
count  3.681200e+04  36812.000000           36812.000000
mean   5.602558e+12    120.834550               1.005487
std    1.691035e+12    152.670425               0.086101
min    1.183560e+12      1.920000               1.000000
25%    5.048806e+12     49.990000               1.000000
50%    6.381719e+12     60.350000               1.000000
75%    7.050673e+12     85.790000               1.000000
max    7.297975e+12   3507.540000               5.000000

In [ ]:
def find_boundaries(df, variable,q1=0.05,q2=0.95):
    # the boundaries are the quantiles
    lower_boundary = df[variable].quantile(q1) # lower quantile
    upper_boundary = df[variable].quantile(q2) # upper quantile
    return upper_boundary, lower_boundary
def capping_outliers(df,variable):
    upper_boundary,lower_boundary =  find_boundaries(df,variable)
    df[variable] = np.where(df[variable] > upper_boundary, upper_boundary,
                       np.where(df[variable] < lower_boundary, lower_boundary, df[variable]))

#Check out top customers

In [ ]:
# Filter out the unwanted product titles before the groupby operation
EC_filtered = EC[~EC['variant_sku'].isin(['SQ3100795', 'SQ5173256'])]

# Group by 'customer_id', 'customer_cohort_month', and 'variant_sku' then count the number of records
customer_record_counts = EC_filtered.groupby(['customer_id', 'customer_cohort_month', 'variant_sku']).size().reset_index(name='record_count')

# Get the top 15 customer IDs by record count in descending order
top_customers = customer_record_counts.nlargest(15, 'record_count')

# drop duplicates
top_customers = top_customers.drop_duplicates(subset='customer_id')

# Merge top_customers with the filtered dataframe to include customer emails and product titles.
# left join to ensure all top customers are included in the final DataFrame even if they have no matching records in EC_filtered
top_customers_info = top_customers.merge(
    EC_filtered[['customer_id', 'customer_cohort_month', 'variant_sku', 'customer_email', 'product_title']],
    on=['customer_id', 'customer_cohort_month', 'variant_sku'],
    how='left'
)

# Select columns we're interested in and drop duplicates
top_customers_info = top_customers_info[['customer_id', 'customer_email', 'product_title', 'variant_sku', 'customer_cohort_month', 'record_count']].drop_duplicates(subset='customer_id')

print(top_customers_info)



       customer_id             customer_email                      product_title  variant_sku customer_cohort_month  record_count
0    6543258091635               na@caroo.com               Singapore Money Tree      BB1352P               2023-03            40
40   1183917604979    EKominowski@outlook.com                     Bloomsy Deluxe    SQ1726938               2018-07            39
79   5566671978611          melbpea@gmail.com                      Bloomsy Roses      SQBRM24               2022-02            26
105  5466754187379       sstuart105@gmail.com                   Bloomsy Original    SQ9178530               2021-12            23
128  6244825202803  Myrna.Flores@azervets.com                    Pet-Safe Blooms  BB-PET-SAFE               2022-09            18
146  2292822999155      lla@adlawcolorado.com                   Bloomsy Original    SQ9178530               2019-09            17
163  2759191396467  jandrews@briarcliffkc.com                    Bloomsy Premium    SQ8862

In [ ]:
EC.describe()

customer_id    total_sales  ordered_item_quantity
count  1.319740e+05  131974.000000          131974.000000
mean   5.521828e+12      36.996985               0.521542
std    1.744121e+12     102.386686               0.503346
min    1.183560e+12   -1652.680000               0.000000
25%    3.616664e+12       0.000000               0.000000
50%    6.368844e+12       0.000000               1.000000
75%    7.022271e+12      47.950000               1.000000
max    7.297975e+12    3507.540000               5.000000

In [ ]:
# Replace 'data' with the actual name of your dataframe
count_zero_sales = (EC['total_sales'] == 0.00).sum()
print(count_zero_sales)


0


In [ ]:
# Assuming 'EC' is the name of your DataFrame
zero_total_sales_count = (EC['total_sales'] == 0.00).sum()
print(f"Number of rows with 0.00 in total_sales: {zero_total_sales_count}")


Number of rows with 0.00 in total_sales: 0


In [ ]:
# Count the number of rows where 'ordered_item_quantity' is 0
zero_quantity_count = (EC['ordered_item_quantity'] == 0).sum()
print(f"Number of orders with 0 item quantity: {zero_quantity_count}")

# Count the number of rows where 'total_sales' is 0
zero_sales_count = (EC['total_sales'] == 0).sum()
print(f"Number of orders with 0 total sales: {zero_sales_count}")


Number of orders with 0 item quantity: 0
Number of orders with 0 total sales: 0


In [ ]:
# Count the number of rows where 'total_sales' is within a very small range around 0
# This handles cases where 'total_sales' might be a very small number close to 0,
# but not exactly 0 due to floating-point arithmetic.
count_zero_sales = np.isclose(EC['total_sales'], 0, atol=1e-8).sum()
print(count_zero_sales)


68080


#Add table from Ship Station in order to look up fo the missing information

In [ ]:
# Load the dataset from the provided URL
ss_df = pd.read_csv('https://raw.githubusercontent.com/Requenamar3/Data-Mining/main/SS.csv')

# Display the first few rows of the dataframe to understand its structure
ss_df.head()

Date - Shipped Date Market - Store Name Market - Markeplace Name     Date - Order Date Custom - Field 3            Customer Email Ship To - City Custom - Field 1   Custom - Field 2   Item - SKU Ship To - Postal Code Order - Number Item - Name Ship To - State  Item - Qty Carrier - Service Selected
0  10/31/2023 12:00:00 AM  BloomsyBox Shopify                  Shopify   8/3/2023 2:49:14 PM       11-01-2023             JDJVJ@AOL.COM  FT LAUDERDALE          4.MIAMI  ORIGINAL_PLEGABLE    SQ9178530            33316-3228         776024    ORIGINAL              FL           1       FedEx Home Delivery®
1  10/31/2023 12:00:00 AM  BloomsyBox Shopify                  Shopify  8/22/2023 9:48:07 AM       11-01-2023  mary.c.parker@ttuhsc.edu        LUBBOCK          2.TEXAS             DELUXE  BB-SG-MIXED            79416-1340         783802      DELUXE              TX           1       FedEx Home Delivery®
2  10/31/2023 12:00:00 AM  BloomsyBox Shopify                  Shopify  9/4/2023 12:56:49 PM       11-01-2023             ajbroc@me.com      CHAPPAQUA     3.NEW JERSEY             DELUXE  BB-SG-MIXED            10514-1302         789981      DELUXE              NY           1       FedEx Home Delivery®
3  10/31/2023 12:00:00 AM  BloomsyBox Shopify                  Shopify  9/5/2023 11:59:05 AM       11-01-2023      bndudley52@gmail.com     SCOTTSDALE     5.CALIFORNIA            PREMIUM    SQ8862610            85255-7165         790118     PREMIUM              AZ           1      OnTrac Ground Service
4  10/31/2023 12:00:00 AM  BloomsyBox Shopify                  Shopify  9/5/2023 11:59:05 AM       11-01-2023      bndudley52@gmail.com     SCOTTSDALE     5.CALIFORNIA            PREMIUM          NaN            85255-7165         790118        cs15              AZ           1      OnTrac Ground Service

In [ ]:
ss_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 469 entries, 0 to 468
Data columns (total 16 columns):
 #   Column                      Non-Null Count  Dtype 
---  ------                      --------------  ----- 
 0   Date - Shipped Date         469 non-null    object
 1   Market - Store Name         469 non-null    object
 2   Market - Markeplace Name    469 non-null    object
 3   Date - Order Date           469 non-null    object
 4   Custom - Field 3            469 non-null    object
 5   Customer Email              446 non-null    object
 6   Ship To - City              469 non-null    object
 7   Custom - Field 1            451 non-null    object
 8   Custom - Field 2            377 non-null    object
 9   Item - SKU                  455 non-null    object
 10  Ship To - Postal Code       469 non-null    object
 11  Order - Number              469 non-null    object
 12  Item - Name                 469 non-null    object
 13  Ship To - State             469 non-null    object

In [ ]:
ss_df.columns


Index(['Date - Shipped Date', 'Market - Store Name', 'Market - Markeplace Name', 'Date - Order Date', 'Custom - Field 3', 'Customer Email', 'Ship To - City', 'Custom - Field 1', 'Custom - Field 2', 'Item - SKU', 'Ship To - Postal Code', 'Order - Number', 'Item - Name', 'Ship To - State', 'Item - Qty', 'Carrier - Service Selected'], dtype='object')

In [ ]:
# Merge EC_df with ss_df on the 'order_name' column in EC_df and 'Order Number' in ss_df
# Make sure the column names are exactly as they appear in your dataframes
ECSS = EC.merge(ss_df[['Custom - Field 3', 'Customer Email', 'Item - SKU', 'Order - Number', 'Item - Name', 'Ship To - State', 'Carrier - Service Selected']],
                        left_on='order_name', right_on='Order - Number', how='left')

# # Now merged_df has the original EC_df data along with the additional columns from ss_df
# # You can then drop the 'Order - Number' column if it's no longer needed
# merged_df.drop('Order - Number', axis=1, inplace=True)

# # If you only want to keep rows where data was successfully merged and no NaN values exist in the new columns, you can do this:
# merged_df.dropna(subset=['Custom - Field 3', 'Customer Email', 'Item - SKU', 'Item - Name', 'Ship To - State', 'Carrier - Service Selected'], inplace=True)

# Save the merged dataframe to a new CSV file or use it for further analysis
# merged_df.to_csv('merged_dataframe.csv', index=False)

ECSS.head()  # Display the first few rows of the merged dataframe


month    financial_status order_name             customer_email customer_type    customer_id variant_sku   product_title shipping_postal_code shipping_region customer_cohort_month  total_sales  ordered_item_quantity Custom - Field 3 Customer Email Item - SKU Order - Number Item - Name Ship To - State Carrier - Service Selected
0  2023-11                paid     826267        amansndrs@gmail.com     Returning  6816167329907         NaN             NaN                71254       Louisiana               2023-08         0.00                      0              NaN            NaN        NaN            NaN         NaN             NaN                        NaN
1  2023-11                paid     821120          jsajcat@gmail.com     Returning  6882693939315   SQ1726938  Bloomsy Deluxe                60101        Illinois               2023-09        76.98                      1              NaN            NaN        NaN            NaN         NaN             NaN                        NaN
2  2023-11                paid     825181        amymattey@gmail.com     Returning  3492230627443         NaN             NaN                44035            Ohio               2020-11        83.88                      0              NaN            NaN        NaN            NaN         NaN             NaN                        NaN
3  2023-11  partially_refunded     793583  kathryndonnelly@yahoo.com     Returning  6536856797299         NaN             NaN                60555        Illinois               2023-03      -162.24                      0              NaN            NaN        NaN            NaN         NaN             NaN                        NaN
4  2023-11  partially_refunded     814967  nancynetherland@gmail.com     Returning  5686113435763         NaN             NaN                98502      Washington               2022-05       -91.44                      0              NaN            NaN        NaN            NaN         NaN             NaN                        NaN

In [ ]:
ECSS.columns

Index(['month', 'financial_status', 'order_name', 'customer_email', 'customer_type', 'customer_id', 'variant_sku', 'product_title', 'shipping_postal_code', 'shipping_region', 'customer_cohort_month', 'total_sales', 'ordered_item_quantity', 'Custom - Field 3', 'Customer Email', 'Item - SKU', 'Order - Number', 'Item - Name', 'Ship To - State', 'Carrier - Service Selected'], dtype='object')

In [ ]:
ECSS.isnull().sum()

month                              0
financial_status                   0
order_name                         0
customer_email                  3049
customer_type                      0
customer_id                        0
variant_sku                    63281
product_title                  63264
shipping_postal_code               1
shipping_region                    1
customer_cohort_month              0
total_sales                        0
ordered_item_quantity              0
Custom - Field 3              131970
Customer Email                131970
Item - SKU                    131970
Order - Number                131970
Item - Name                   131970
Ship To - State               131970
Carrier - Service Selected    131970
dtype: int64

In [ ]:
df.dropna(inplace=True)  # inplace=True means we dropped them permanently

In [ ]:
df.isnull().sum()

InvoiceNo      0
StockCode      0
Description    0
Quantity       0
InvoiceDate    0
UnitPrice      0
CustomerID     0
Country        0
dtype: int64